In [39]:
import sys
!{sys.executable} -m pip install numpy pandas==1.3.5 transformers Bio-Epidemiology-NER
!{sys.executable} -m pip install scikit-learn matplotlib nltk word2number sentence_transformers scipy owlready2

  Using cached owlready2-0.45.tar.gz (27.3 MB)
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
  Created wheel for owlready2: filename=owlready2-0.45-cp38-cp38-linux_x86_64.whl size=24278819 sha256=83194a6a88932369ecacf2132ca4bf07f27e198e6f65240ea118e9cec9256ba2
  Stored in directory: /home/romi/.cache/pip/wheels/59/8a/7d/ae6990c9462d314faa57aa1be2c8a23146da2ca9f1e1f29038
Successfully built owlready2


In [25]:
!{sys.executable} -m pip install torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cu118

Looking in indexes: https://download.pytorch.org/whl/cu118
     |████████████████████████████████| 6.2 MB 4.8 MB/s eta 0:00:01
     |████████████████████████████████| 3.3 MB 43.7 MB/s eta 0:00:01


In [11]:
#load libraries
import os
# os.kill(os.getpid(), 9)

from transformers import pipeline
from transformers import AutoTokenizer, AutoModelForTokenClassification
import pandas as pd
import numpy as np
import Bio_Epidemiology_NER as bioNER
import math

In [2]:
#load transformer tokenizer and model
tokenizer = AutoTokenizer.from_pretrained("d4data/biomedical-ner-all")
model = AutoModelForTokenClassification.from_pretrained("d4data/biomedical-ner-all")

config.json:   0%|          | 0.00/5.00k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/266M [00:00<?, ?B/s]

# Data and model analysis

In [18]:
# import pandas as pd
#load and visualize example csv
data = pd.read_csv("../../data/diabetes-studies-addinfo.csv")
data.head()

Study Title  \
0            Renal Mechanism of Action/Splay vs. TmG   
1             Novel Biomarker for Development of T2D   
2  BM-MNC and UCMSC for Type 2 Diabetes Mellitus ...   
3  The Influence of Health Beliefs and Uncertaint...   
4  Dose Response of Eccentric Exercise on Glycemi...   

                            Primary Outcome Measures  \
0  The change in urinary glucose excretion dynami...   
1  Relationship between 11β-HSD1 and 5α-reductase...   
2  Decreasing total daily dose of insulin (>= 30%...   
3  Insulin adherence, Average number of positive ...   
4  Glucometer, Glucometer will use to monitor glu...   

                          Secondary Outcome Measures Other Outcome Measures  \
0  Differences in urinary glucose between healthy...                    NaN   
1  Relationship between 11β-HSD1 and 5α-reductase...                    NaN   
2  Increasing of C-peptide level, Measurements we...                    NaN   
3                                                NaN                    NaN   
4  WHO-QOL (BREF-Urdu version), WHOQOL-BREF is a ...                    NaN   

        nct_id   startDate      status      study_type                phases  
0  NCT00726505     2009-06  TERMINATED  INTERVENTIONAL            ['PHASE1']  
1  NCT02326129     2015-02   COMPLETED   OBSERVATIONAL                ['NA']  
2  NCT04501341  2016-03-14     UNKNOWN  INTERVENTIONAL  ['PHASE1', 'PHASE2']  
3  NCT02074540     2014-04     UNKNOWN   OBSERVATIONAL                ['NA']  
4  NCT04790526  2021-07-12   COMPLETED  INTERVENTIONAL                ['NA']

In [36]:
def ner_on_df(data):
    result = pd.DataFrame(columns = ['entity_group', 'value', 'score', 'from','nct_id'])

    for i,row in data.iterrows():
        # print(row)
        out = pd.DataFrame(columns = ['entity_group', 'value', 'score', 'from'])

        if isinstance(row['Primary Outcome Measures'],str):
            for split in row['Primary Outcome Measures'].split('|'):
                out1 = bioNER.bio_recognizer.ner_prediction(corpus=split,compute='cpu') #pass compute='gpu' if using gpu
                out1['from'] = 'primary'
                # print(out1)
                
                out = out.append(out1,ignore_index=True)


            # print(out)
            # print(row['Primary Outcome Measures'])
        
        if isinstance(row['Secondary Outcome Measures'],str):
            for split in row['Secondary Outcome Measures'].split('|'):
                out1 = bioNER.bio_recognizer.ner_prediction(corpus=split,compute='cpu') #pass compute='gpu' if using gpu
                out1['from'] = 'secondary'
                # print(out1)
                out = out.append(out1,ignore_index=True)
            # print(row['Secondary Outcome Measures'])
        
        
        if isinstance(row['Other Outcome Measures'],str):
            for split in row['Secondary Outcome Measures'].split('|'):
                out1 = bioNER.bio_recognizer.ner_prediction(corpus=split,compute='cpu') #pass compute='gpu' if using gpu
                out1['from'] = 'other'
                # print(out1)
                out = out.append(out1,ignore_index=True)

        out['nct_id'] = row['nct_id']
        result = result.append(out)
        # print(result)
        # break
    
    return result

/home/romi/.local/lib/python3.8/site-packages/transformers/pipelines/token_classification.py:168: UserWarning: `grouped_entities` is deprecated and will be removed in version v5.0.0, defaulted to `aggregation_strategy="simple"` instead.
  warnings.warn(


             entity_group            value     score       from       nct_id
0    Detailed_description          urinary  0.976973    primary  NCT00726505
1    Diagnostic_procedure          glucose  0.998006    primary  NCT00726505
2                    Date     after 7 days  0.980263    primary  NCT00726505
3   Therapeutic_procedure        treatment  0.932885    primary  NCT00726505
4               Lab_value      Differences  0.957372  secondary  NCT00726505
5    Diagnostic_procedure  urinary glucose  0.928494  secondary  NCT00726505
6    Detailed_description          healthy  0.743920  secondary  NCT00726505
7                    Date           7 days  0.999584  secondary  NCT00726505
8    Diagnostic_procedure            liver  0.691329  secondary  NCT00726505
9    Diagnostic_procedure          glucose  0.667786  secondary  NCT00726505
10                   Time          one day  0.964558  secondary  NCT00726505
11   Diagnostic_procedure          Glucose  0.416617  secondary  NCT00726505

In [29]:
#visualize the obtained csv file from the NER model
csv_data = pd.read_csv(r"C:\Users\vivia\Downloads\ctg_pdf_df.csv")
csv_data.head()

Unnamed: 0          Entity Group                  Value     Score  Page  \
0           0                  Date  7 7 days days|Changes  0.986228     1   
1           1  Detailed_description                healthy  0.538863     1   
2           2                  Date                    7 7  0.974785     1   
3           3  Diagnostic_procedure                  liver  0.681459     1   
4           4                  Date                one one  0.848752     1   

                               Pdf File  
0  C:\Users\vivia\Downloads\ctg_pdf.pdf  
1  C:\Users\vivia\Downloads\ctg_pdf.pdf  
2  C:\Users\vivia\Downloads\ctg_pdf.pdf  
3  C:\Users\vivia\Downloads\ctg_pdf.pdf  
4  C:\Users\vivia\Downloads\ctg_pdf.pdf

In [15]:
csv_data["Entity Group"]

0                      Date
1      Detailed_description
2                      Date
3      Diagnostic_procedure
4                      Date
               ...         
871    Diagnostic_procedure
872    Diagnostic_procedure
873    Diagnostic_procedure
874    Detailed_description
875    Detailed_description
Name: Entity Group, Length: 876, dtype: object

In [30]:
#delete unused columns
final_data = csv_data.drop(labels = ['Unnamed: 0', "Score", 'Page', 'Pdf File'], axis = 1)
final_data[45:80]

Entity Group                                              Value
45   Diagnostic_procedure                                              serum
46   Diagnostic_procedure                                        supernatant
47   Diagnostic_procedure                                       PBMC Patient
48   Diagnostic_procedure                                               PBMC
49                   Date                     month month month month months
50                   Date                                             months
51              Lab_value                                             Stable
52   Diagnostic_procedure            HOMA-IR intervention|HbA1c HbA1c Health
53             Medication                                            Insulin
54   Detailed_description                                          Eccentric
55   Diagnostic_procedure                     Glycemic Glucometer Glucometer
56   Diagnostic_procedure                                   Glycemic Control
57   Detailed_description                                          Type Type
58   Diagnostic_procedure             Glucometer Guidelines V-Go FPG Glucose
59   Diagnostic_procedure           Glucometer week|Dynamometer dynamometers
60                   Date  12 12th 12th 12th 12th W11/12 12 12 12 12 12 1...
61   Diagnostic_procedure  week|HBA1c A1C A1C A1C A1C months|A1c A1C HbA1...
62       Disease_disorder  Type Type Type Type Type II II Diabetes Diabet...
63                   Date                                 0 WHOQOL-100 0 0 0
64                   Date                                12th 12th 12th 12th
65   Diagnostic_procedure         WHO-QOL WHOQOL-BREF WHOQOL-100 WHO-QoL WHO
66   Diagnostic_procedure                              BREF-Urdu WHOQOL-BREF
67   Detailed_description                                    version version
68   Diagnostic_procedure                             WHOQOL-BREF WHOQOL-100
69   Detailed_description                        week|Six Six-minute Minutes
70   Diagnostic_procedure                                walk test test test
71   Diagnostic_procedure                                              6-MWT
72   Diagnostic_procedure                                    cardiopulmonary
73  Therapeutic_procedure                                   week|Dynamometer
74   Diagnostic_procedure                                  strength strength
75   Diagnostic_procedure                      limb muscle strength strength
76             Medication                     Insulin months|Insulin Insulin
77   Detailed_description                                            V-Go Â®
78       Disease_disorder  Type Type Type Type Type 12 T2DM 12th 12th 12t...
79            Coreference                                              Bolus

In [31]:
#obtain column entity group with only the diangostic procedure entities
target_value = 'Diagnostic_procedure'
filtered_df = final_data.loc[final_data['Entity Group'] == target_value]
print(filtered_df)

             Entity Group                                              Value
3    Diagnostic_procedure                                              liver
6    Diagnostic_procedure  11Î²-HSD1 11Î²-HSD1 11Î²-HSD1 11Î²-HSD1 11Î²-HSD1
7    Diagnostic_procedure            insulin insulin insulin insulin insulin
11   Diagnostic_procedure                                  pubertal pubertal
12   Diagnostic_procedure                                      status status
..                    ...                                                ...
867  Diagnostic_procedure                                     walk test test
868  Diagnostic_procedure                                    cardiopulmonary
871  Diagnostic_procedure                                  strength strength
872  Diagnostic_procedure                                               body
873  Diagnostic_procedure                           muscle strength strength

[319 rows x 2 columns]


In [44]:
#save dataframe to CSV file
filtered_df.to_csv(r"C:\Users\vivia\Downloads\Diagnostic_data.csv", index=False)


# Model on 1000 CTG studies

In [20]:
#load the 1000 clinical tr
data4 = pd.read_csv(r"C:\Users\vivia\Downloads\ctg-studies (4).csv", encoding="latin1")

In [21]:
from Bio_Epidemiology_NER.bio_recognizer import pdf_annotate

pdffile3 = r"C:\Users\vivia\Downloads\ctg-studies (4).pdf"
pdf_annotate(pdffile3,compute='cpu', output_format='csv') #pass compute='gpu' if using gpu

C:\Users\vivia\anaconda3\lib\site-packages\transformers\pipelines\token_classification.py:157: UserWarning: `grouped_entities` is deprecated and will be removed in version v5.0.0, defaulted to `aggregation_strategy="simple"` instead.
  warnings.warn(
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(disease_df) # adding the disease_df to existing
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:100: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  master_df = master_df.append(final_df)
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. 

C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(disease_df) # adding the disease_df to existing
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:100: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  master_df = master_df.append(final_df)
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(disease_df) # adding the disease_df to existing
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:100: FutureWarning: The frame.append method is deprecated and wil

C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(disease_df) # adding the disease_df to existing
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:100: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  master_df = master_df.append(final_df)
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(disease_df) # adding the disease_df to existing
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:100: FutureWarning: The frame.append method is deprecated and wil

C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(disease_df) # adding the disease_df to existing
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:100: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  master_df = master_df.append(final_df)
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(disease_df) # adding the disease_df to existing
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:100: FutureWarning: The frame.append method is deprecated and wil

C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(disease_df) # adding the disease_df to existing
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:100: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  master_df = master_df.append(final_df)
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(disease_df) # adding the disease_df to existing
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:100: FutureWarning: The frame.append method is deprecated and wil

...

C:\Users\vivia\anaconda3\lib\site-packages\transformers\pipelines\token_classification.py:157: UserWarning: `grouped_entities` is deprecated and will be removed in version v5.0.0, defaulted to `aggregation_strategy="simple"` instead.
  warnings.warn(
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(disease_df) # adding the disease_df to existing
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:100: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  master_df = master_df.append(final_df)
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. 

C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(disease_df) # adding the disease_df to existing
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:100: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  master_df = master_df.append(final_df)
C:\Users\vivia\anaconda3\lib\site-packages\transformers\pipelines\token_classification.py:157: UserWarning: `grouped_entities` is deprecated and will be removed in version v5.0.0, defaulted to `aggregation_strategy="simple"` instead.
  warnings.warn(
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. 

C:\Users\vivia\anaconda3\lib\site-packages\transformers\pipelines\token_classification.py:157: UserWarning: `grouped_entities` is deprecated and will be removed in version v5.0.0, defaulted to `aggregation_strategy="simple"` instead.
  warnings.warn(
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(disease_df) # adding the disease_df to existing
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:100: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  master_df = master_df.append(final_df)
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. 

C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(disease_df) # adding the disease_df to existing
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:100: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  master_df = master_df.append(final_df)
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:94: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(disease_df) # adding the disease_df to existing
C:\Users\vivia\anaconda3\lib\site-packages\Bio_Epidemiology_NER\bio_recognizer.py:100: FutureWarning: The frame.append method is deprecated and wil

Entity Group  \
0                      Date   
1      Detailed_description   
2                      Date   
3      Diagnostic_procedure   
4                      Date   
...                     ...   
85968  Diagnostic_procedure   
85969  Detailed_description   
85970  Diagnostic_procedure   
85971      Disease_disorder   
85972      Disease_disorder   

                                                   Value     Score  Page  \
0                                  7 7 days days|Changes  0.986228     1   
1                                                healthy  0.538863     1   
2                                                    7 7  0.974785     1   
3                                                  liver  0.681459     1   
4                                                one one  0.848752     1   
...                                                  ...       ...   ...   
85968                                            Glucose  0.997353   504   
85969                                         Continuous  0.996820   504   
85970                                            glucose  0.983149   504   
85971                                treatment Time meas  0.774983   504   
85972  last was Baseline Baseline as Measured invasiv...  0.689853   504   

                                           Pdf File  
0      C:\Users\vivia\Downloads\ctg-studies (4).pdf  
1      C:\Users\vivia\Downloads\ctg-studies (4).pdf  
2      C:\Users\vivia\Downloads\ctg-studies (4).pdf  
3      C:\Users\vivia\Downloads\ctg-studies (4).pdf  
4      C:\Users\vivia\Downloads\ctg-studies (4).pdf  
...                                             ...  
85968  C:\Users\vivia\Downloads\ctg-studies (4).pdf  
85969  C:\Users\vivia\Downloads\ctg-studies (4).pdf  
85970  C:\Users\vivia\Downloads\ctg-studies (4).pdf  
85971  C:\Users\vivia\Downloads\ctg-studies (4).pdf  
85972  C:\Users\vivia\Downloads\ctg-studies (4).pdf  

[85973 rows x 5 columns]

In [22]:
#load obtained csv file from the pdf annotation function
csv_data = pd.read_csv(r"C:\Users\vivia\Downloads\ctg-studies (4)_df.csv")

In [8]:
#drop unused columns and obtain only the 'Diangostic Procedure' entities
final_data = csv_data.drop(labels = ['Unnamed: 0', "Score", 'Page', 'Pdf File'], axis = 1)
target_value = 'Diagnostic_procedure'
filtered_df = final_data.loc[final_data['Entity Group'] == target_value]
#save the dataframe to a new CSV file
filtered_df.to_csv(r"C:\Users\vivia\Downloads\1000Diagnostic_data.csv", index=False)

# Remove duplicates

In [1]:
import pandas as pd

In [4]:
#load entity list from analyzing 1000 clinical trials
df = pd.read_csv(r"C:\Users\vivia\Downloads\1000Diagnostic_data.csv")

In [5]:
#define target column
column_name = 'Value'

In [6]:
#drop duplicate values in target column
df.drop_duplicates(subset = column_name, inplace = True)

In [8]:
#save dataframe to csv
df.to_csv(r"C:\Users\vivia\Downloads\no_duplicate_1000Diagnostic_data.csv", index = False)